In [ ]:
import pandas as pd
import os

In [ ]:
root_path = r"E:/data/ag"
output_path = r"E:/data/ag/ag888.csv"
# df_tmp = pd.read_csv('E:/data/rb/rb888_2023.csv',encoding="utf-8")

In [ ]:
files = []

for r, ds, fs in os.walk(root_path):
    for f in fs:
        # if f[0:4] == '2023':
        abs_filepath = os.path.join(r, f)
        files.append(abs_filepath)
files = sorted(files)

df = pd.DataFrame()
for f in files:
    df_temp = pd.read_csv(
        f,
        usecols=[0, 1, 2, 5, 12, 21, 22, 23, 24, 25, 26, 44],
        names=[
            "交易日",
            "统一代码",
            "合约代码",
            "最新价",
            "数量",
            "最后修改时间",
            "最后修改毫秒",
            "申买价一",
            "申买量一",
            "申卖价一",
            "申卖量一",
            "业务日期",
        ],
        skiprows=1,
        encoding="utf-8",
    )
    # df_temp = pd.read_csv(f, usecols=[0,5], names=[
    #                  'datetime',  'volume'])
    df = pd.concat([df, df_temp])

In [ ]:
df.tail()

In [ ]:
df.head()

In [ ]:
#df_tmp = pd.read_csv('E:/data/rb/rb888_2023.csv',encoding="utf-8")
#df_tmp.tail()
#df_tmp.tail().to_csv("E:/data/rb/rb_tail.csv",index= False)

In [ ]:
df.reset_index(drop=True, inplace=True)

In [ ]:
df.info()
# 21754840

In [ ]:
import numpy as np

In [ ]:
df.loc[2493107:2493111]

In [ ]:
# 等比复权,先不考虑
# df['复权因子'] = df['卖一价'].shift() / df['买一价']
df['复权因子'] = np.where(df['合约代码'] != df['合约代码'].shift(), df['卖一价'].shift() / df['买一价'], 1)
df['复权因子'] = df['复权因子'].fillna(1)
# df['复权因子'].loc[0] = 1
df['买一价_adj'] = df['买一价'] * df['复权因子'].cumprod()
df['卖一价_adj'] = df['卖一价'] * df['复权因子'].cumprod()
df['最新_adj'] = df['最新'] * df['复权因子'].cumprod()
# df['low_adj'] = df['low'] * adjust.cumprod()
# df['high_adj'] = df['high'] * adjust.cumprod()

In [ ]:
# 等差复权
df['复权因子'] = np.where(df['合约代码'] != df['合约代码'].shift(), df['申卖价一'].shift() - df['申买价一'], 0)
df['复权因子'] = df['复权因子'].fillna(0)
# df['复权因子'].loc[0] = 1
df['申买价一_adj'] = df['申买价一'] + df['复权因子'].cumsum()
df['申卖价一_adj'] = df['申卖价一'] + df['复权因子'].cumsum()
df['最新价_adj'] = df['最新价'] + df['复权因子'].cumsum()
# df['low_adj'] = df['low'] + df['复权因子'].cumsum()
# df['high_adj'] = df['high'] + df['复权因子'].cumsum()

In [ ]:
df.loc[391880:391890]

In [ ]:
df['申买价一'] = df['申买价一_adj']
df['申卖价一'] = df['申卖价一_adj']
df['最新价'] = df['最新价_adj']

In [ ]:
df.loc[391880:391890]

In [ ]:
non_zero_indices = df[df['复权因子'] != 0].index

In [ ]:
print(non_zero_indices)

In [ ]:
# df.drop('复权因子', axis=1)
# df.drop('买一价_adj', axis=1)
# df.drop('卖一价_adj', axis=1)
del df['复权因子']
del df['申买价一_adj']
del df['申卖价一_adj']
del df['最新价_adj']

In [ ]:
df.loc[391880:391890]

In [ ]:
df.to_csv(output_path, index=False)

In [ ]:
df.head().to_csv("E:/data/rb/rb_ch_temp.csv")

In [ ]:
drop_index1 = df.query('最后修改时间>"15:00:00" & 最后修改时间<"21:00:00"')[
    "最后修改时间"
].index
# drop_index1 = df.query('最后修改时间>"15:00:00"')["最后修改时间"].index
# drop_index2 = df.query('最后修改时间>"01:00:00" & 最后修改时间<"09:00:00"')["最后修改时间"].index
# drop_index2 = df.query('最后修改时间>"01:00:00" & 最后修改时间<"09:00:00"')["最后修改时间"].index
drop_index2 = df.query('最后修改时间<"09:00:00"')["最后修改时间"].index
drop_index3 = df.query('最后修改时间>"23:00:00" & 最后修改时间<"23:59:59"')[
    "最后修改时间"
].index
drop_index4 = df.query('最后修改时间>"11:30:00" & 最后修改时间<"13:30:00"')[
    "最后修改时间"
].index

In [ ]:
df.drop(labels=drop_index1, axis=0, inplace=True)
df.drop(drop_index2, axis=0, inplace=True)
df.drop(drop_index3, axis=0, inplace=True)
df.drop(drop_index4, axis=0, inplace=True)

In [ ]:
df.tail()

In [ ]:
df.info()

In [ ]:
df.reset_index(drop=True, inplace=True)

In [ ]:
df["datetime"] = pd.to_datetime(
    pd.to_datetime(df["交易日"].astype(str)).astype(str)
    + " "
    + df["最后修改时间"].astype(str)
    + "."
    + df["最后修改毫秒"].astype(str)
)

In [ ]:
df.tail()

In [ ]:
df.rename(
    columns={
        "最新价": "lastprice",
        "数量": "volume",
        "申买价一": "bid_p",
        "申买量一": "bid_v",
        "申卖价一": "ask_p",
        "申卖量一": "ask_v",
        "合约代码": "symbol",
    },
    inplace=True,
)

In [ ]:
df["vol_diff"] = df["volume"].diff()

In [ ]:
df.head()

In [ ]:
df.loc[df["vol_diff"].isnull(), "vol_diff"] = df.loc[df["vol_diff"].isnull(), "volume"]

In [ ]:
df["volume"] = df["vol_diff"]

In [ ]:
df.to_csv(output_path)